### Target Challenge
#### Silicon Slayers


### 1. Target
Our target is the number of people attending church for each census tract. We start with filtering the data frame down to just Churches by filtering by location name. We also take out the temples by using their specific addresses. Next we take our newly filtered data and organize it by census tract. We can do this because the data gives us the home census tract for each visitor at the church buildings. After that we calculate Sunday attendance by multiplying the total visitors for each census tract by the ratio of Sunday visits compared to the rest of the week. Finally we verify our results by making sure we have 298 tracts(the number of census tracts in Idaho) and graphing our results.

### 2. Pseudocode
- Load data and packages
- Filter places for LDS churches with reg ex 
- Filter out the Temples
- Join Filter places table to patterns table
- Isolate the month from the date_range_start column and create a month column
- Select needed columns and explode the visitor_home_aggregation
- Create scaled visitors column(logic is tract_visitors * (normalized_visits_by_state_scaling/raw_visit_counts))
- Collect the ratio of Sunday visits to the other weekdays and multiply that number to our new scaled visitors
- Group by tract and month and sum total scaled visitors
- Plot and explore!

In [0]:
# Load libraries
import pyspark.sql.functions as F
import requests
import shutil
import pandas as pd
import plotly.express as px

In [0]:
# Read data
patterns = spark.read.parquet('dbfs:/data/idaho/patterns')
places = spark.read.parquet('dbfs:/data/idaho/places.parquet')
temples = spark.read.parquet('dbfs:/FileStore/temple_details_2.parquet')

Filter to only the Church of Jesus Christ of Latter day Saints

In [0]:
# 384 Rows (exact match), 406 Rows (levenshtein, LDS matches, and excluding temples)
# My original code, replaced by Hathaway's
my_churches = places.filter(
    (places.location_name == 'LDS Church') | 
    (places.location_name == 'Church of Jesus Christ LDS') |
    (F.levenshtein(F.lit("The Church of Jesus Christ of Latter day Saints"), F.col("location_name")) < 10)
)

In [0]:
idaho_temples = places.filter(
    ((places.street_address == '750 S 2nd E') & (places.city == 'Rexburg')) | 
    ((places.street_address == '1000 Memorial Dr') & (places.city == 'Idaho Falls')) | 
    ((places.street_address == '3100 Butte St') & (places.city == 'Pocatello')) | 
    ((places.street_address == '1405 Eastland Dr N') & (places.city == 'Twin Falls')) | 
    ((places.street_address == '1211 S Cole Rd') & (places.city == 'Boise')) |
    ((places.street_address == '7355 N Linder Rd') & (places.city == 'Meridian'))
)

In [0]:
hathaway_churches = places.filter(
    (F.col("top_category") == "Religious Organizations") &
    (F.col("location_name").rlike("Latter|latter|Saints|saints|LDS|\b[Ww]ard\b")) &
    (F.col("location_name").rlike("^((?!Reorganized).)*$")) &
    (F.col("location_name").rlike("^((?!All Saints).)*$")) &
    (F.col("location_name").rlike("^((?![cC]ath).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]ody).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]eter).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]atholic).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]res).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]inist).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]ission).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]orship).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]ain).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]aptist).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]eth).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]vang).)*$")) &
    (F.col("location_name").rlike("^((?![Ll]utheran).)*$")) &
    (F.col("location_name").rlike("^((?![Oo]rthodox).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]piscopal).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]abernacle).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]arvest).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ssem).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]edia).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]artha).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]hristian).)*$")) &
    (F.col("location_name").rlike("^((?![Uu]nited).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]esl).)*$")) &
    (F.col("location_name").rlike("^((?![C]cosmas).)*$")) &
    (F.col("location_name").rlike("^((?![Gg]reater).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]rison).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]ommuni).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]lement).)*$")) &
    (F.col("location_name").rlike("^((?![Vv]iridian).)*$")) &
    (F.col("location_name").rlike("^((?![Dd]iocese).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]istory).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]chool).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]hougt).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]oliness).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]artyr).)*$")) &
    (F.col("location_name").rlike("^((?![Jj]ames).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]ellowship).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]ouse).)*$")) &
    (F.col("location_name").rlike("^((?![Gg]lory).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]nglican).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]oetic).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]anctuary).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]quipping).)*$")) &
    (F.col("location_name").rlike("^((?![Jj]ohn).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ndrew).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]manuel).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]edeemed).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]erfecting).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]ngel).)*$")) &
    (F.col("location_name").rlike("^((?![Aa]rchangel).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]icheal).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]hought).)*$")) &
    (F.col("location_name").rlike("^((?![Pp]ariosse).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]osmas).)*$")) &
    (F.col("location_name").rlike("^((?![Dd]eliverance).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]ociete).)*$")) &
    (F.col("location_name").rlike("^((?![Tt]emple).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]eminary).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]mployment).)*$")) &
    (F.col("location_name").rlike("^((?![Ii]nstitute).)*$")) &
    (F.col("location_name").rlike("^((?![Cc]amp).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]tudent).)*$")) &
    (F.col("location_name").rlike("^((?![Ee]ducation).)*$")) &
    (F.col("location_name").rlike("^((?![Ss]ocial).)*$")) &
    (F.col("location_name").rlike("^((?![Ww]welfare).)*$")) &
    (F.col("location_name").rlike("^((?![Cc][Ee][Ss]).)*$")) &
    (F.col("location_name").rlike("^((?![Ff]amily).)*$")) &
    (F.col("location_name").rlike("^((?![Mm]ary).)*$")) &
    (F.col("location_name").rlike("^((?![Rr]ussian).)*$")) &
    (F.col("location_name").rlike("^((?![Bb]eautif).)*$")) &
    (F.col("location_name").rlike("^((?![Hh]eaven).)*$")) &    
    (F.col("location_name").rlike("^((?!Inc).)*$")) &
    (F.col("location_name").rlike("^((?!God).)*$"))
  )
  
hathaway_churches.display()

placekey poi_cbg parent_placekey location_name brands safegraph_brand_ids store_id top_category sub_category naics_code open_hours category_tags latitude longitude street_address city region postal_code iso_country_code opened_on closed_on tracking_closed_since websites phone_number wkt_area_sq_meters zzy-222@5wj-krc-dsq 160499400001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 45.927403 -116.11182 Valley Vw Kamiah ID 83536 US null null 2019-07 [] +12089352842 1362.0 zzw-222@5wq-s83-g8v 160679702001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.557902 -113.792354 241 N Overland Ave Burley ID 83318 US null null 2019-07 ["lds.org"] +12086780434 954.0 222-222@5wf-zyt-rhq 160439703001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.967664 -111.680578 145 E 1st N St. Anthony ID 83445 US null null 2019-07 ["lds.org"] +12086247540 1281.0 223-223@5w9-hwd-5mk 160010102252 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.695074 -116.345195 700 E State St Eagle ID 83616 US null null 2019-07 [] +12089392988 522.0 zzy-222@5ws-j8j-6x5 160419701002 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.100707 -111.871853 213 N 2nd E Preston ID 83263 US null null 2019-07 ["lds.org"] +12088521469 60.0 zzy-222@5wq-s89-9cq null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.537956 -113.794962 213 W Main St Burley ID 83318 US null null 2019-07 ["lds.org"] +12086542591 923.0 222-222@5ws-hhd-zpv null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.230853 -111.95055 7389 N 3000 W Preston ID 83263 US null null 2019-07 ["lds.org"] +12088522768 218.0 zzw-222@5wq-s83-g8v null null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.557902 -113.792354 241 N Overland Ave Burley ID 83318 US null null 2019-07 ["lds.org"] +12086780434 954.0 zzy-222@5wr-7dm-9xq 160830009001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.586804 -114.443502 2085 S Temple Dr Twin Falls ID 83301 US null null 2019-07 ["mormon.org"] +12087333446 2467.0 zzy-222@5w9-jbw-p7q 160010001001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.619514 -116.20184 Shamrock & Mcmillanrd Boise ID 83702 US null null 2019-07 ["lds.org"] +12083773220 1210.0 zzy-222@5ws-hs9-mp9 160419701001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 42.228318 -111.714703 7316 N Capitol Hill Rd Preston ID 83263 US null null 2019-07 ["lds.org"] +12088520477 936.0 zzw-222@5wg-43c-5cq 160119501001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 43.31038 -112.083427 792 N 1090 E Shelley ID 83274 US null null 2019-07 [] +12083575700 1763.0 zzy-222@5w9-th5-gp9 160759603001 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations 813110 null Churches 44.009066 -116.91772 329 S Pennsylvania Ave Fruitland ID 83619 US null null 2019-07 [] +12084524345 328.0 222-222@5wr-2cg-rkz 160539704002 null The Church of Jesus Christ of Latter day Saints null null null Religious Organizations Religious Organizations

In [0]:
# Exclude the temples
churches = hathaway_churches.join(idaho_temples, hathaway_churches.placekey == idaho_temples.placekey, how='left_anti')

### 3. Diagram of tables and columns used to build the feature

In [0]:
# Diagram of Tables and Columns
print("Church Schema: ")
churches.select(
    'placekey',
    'location_name',
).printSchema()
print()
print("Patterns Schema: ")
patterns.select(
    'placekey',
    'date_range_start',
    'raw_visit_counts',
    'popularity_by_day',
    'visitor_home_aggregation',
    'normalized_visits_by_state_scaling',
).printSchema()

Church Schema: 
root
 |-- placekey: string (nullable = true)
 |-- location_name: string (nullable = true)


Patterns Schema: 
root
 |-- placekey: string (nullable = true)
 |-- date_range_start: string (nullable = true)
 |-- raw_visit_counts: double (nullable = true)
 |-- popularity_by_day: map (nullable = true)
 |    |-- key: string
 |    |-- value: integer (valueContainsNull = true)
 |-- visitor_home_aggregation: map (nullable = true)
 |    |-- key: string
 |    |-- value: integer (valueContainsNull = true)
 |-- normalized_visits_by_state_scaling: double (nullable = true)



### 4. Code Snippet of Data Wrangling

In [0]:
""" 
Assumptions: 
The ratio of Sunday to other days is proportionate for different tracts. 
The state scaling ratio is accurate. 
"""
# Filter to just churches
church_patterns = patterns.join(churches, on='placekey', how='leftsemi')

# visitor_home_aggregation
home_agg = church_patterns.select(
    "*", 
    # Explodes the map of census tracts and visitor counts
    F.explode(
        F.col('visitor_home_aggregation')
        ).alias('tract', 'tract_visitors'),    
    # Gets the state scaling ratio
    (F.col('normalized_visits_by_state_scaling')/F.col('raw_visit_counts')).alias('state_scaling'),
    # Multiplies tract visitors by the state scaling ratio to get a more accurate total estimate
    (F.col('tract_visitors') * F.col('state_scaling')).alias('tract_visitors_scaled')
)

home_agg = home_agg.select(
    "*",
    # Gets the ratio of Sunday visits compared to all days of the week visits
    (F.expr(
        """popularity_by_day['Sunday'] / 
        (popularity_by_day['Monday'] 
        + popularity_by_day['Tuesday']
        + popularity_by_day['Wednesday']
        + popularity_by_day['Thursday']
        + popularity_by_day['Friday']
        + popularity_by_day['Saturday']
        + popularity_by_day['Sunday']
           )""")).alias('sunday_ratio'),
    # Calculates the Sunday visits by census tract
    (F.col('tract_visitors_scaled')*F.col('sunday_ratio')).alias('sunday_visitors')
    
)

home_agg.select('tract', 
                F.month(home_agg['date_range_start']).alias('month'),
                'tract_visitors', 
                'state_scaling', 
                'tract_visitors_scaled', 
                'sunday_ratio', 
                'sunday_visitors').display()

Church Schema: 
root
 |-- placekey: string (nullable = true)
 |-- location_name: string (nullable = true)


Patterns Schema: 
root
 |-- placekey: string (nullable = true)
 |-- date_range_start: string (nullable = true)
 |-- raw_visit_counts: double (nullable = true)
 |-- popularity_by_day: map (nullable = true)
 |    |-- key: string
 |    |-- value: integer (valueContainsNull = true)
 |-- visitor_home_aggregation: map (nullable = true)
 |    |-- key: string
 |    |-- value: integer (valueContainsNull = true)
 |-- normalized_visits_by_state_scaling: double (nullable = true)



tract month tract_visitors state_scaling tract_visitors_scaled sunday_ratio sunday_visitors 16001010331 12 32 16.110201850071867 515.5264592022997 0.6436170212765957 331.8016040610546 16001010313 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16001010225 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16001010334 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16027021903 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16015950200 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16001010335 12 4 16.110201850071867 64.44080740028747 0.6436170212765957 41.475200507631826 16065950301 7 4 16.40532143209921 65.62128572839684 0.75 49.21596429629763 16031950600 4 5 15.477198214149562 77.3859910707478 0.0 0.0 16005000400 4 39 15.477198214149562 603.6107303518329 0.4855072463768116 293.05738357661454 16005001601 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 49011127003 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 16005940000 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 16005000800 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 16019970502 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 16077960100 4 4 15.477198214149562 61.90879285659825 0.4855072463768116 30.057167546319437 16073950101 8 9 15.35943805488297 138.23494249394673 0.3181818181818182 43.98384533898305 16001010401 8 5 15.35943805488297 76.79719027441485 0.3181818181818182 24.43546963276836 32003002976 8 4 15.35943805488297 61.43775221953188 0.3181818181818182 19.54837570621469 16027022200 8 4 15.35943805488297 61.43775221953188 0.3181818181818182 19.54837570621469 16001010223 8 4 15.35943805488297 61.43775221953188 0.3181818181818182 19.54837570621469 16001010100 4 9 15.47719821414956 139.29478392734603 0.017241379310344827 2.401634205643897 16001000202 4 7 15.47719821414956 108.34038749904693 0.017241379310344827 1.867937715500809 53053070703 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16001000304 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16001000201 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16027022300 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 53033025803 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16001000600 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16001000302 4 4 15.47719821414956 61.90879285659824 0.017241379310344827 1.0673929802861766 16073950101 3 9 16.056397816858702 144.5075803517283 0.46551724137931033 67.27077016373559 16027022200 3 4 16.056397816858702 64.22559126743481 0.46551724137931033 29.898120072771377 16029960200 2 23 15.979296772500653 367.523825767515 0.007575757575757576 2.7842714073296593 16029960100 2 17 15.979296772500653 271.64804513251113 0.007575757575757576 2.057939735852357 16007950100 2 8 15.979296772500653 127.83437418000523 0.007575757575757576 0.9684422286364033 16007950200 2 7 15.979296772500653 111.85507740750458 0.007575757575757576 0.8473869500568529 16045960200 7 4 16.40532143209921 65.62128572839684 0.3333333333333333 21.873761909465614 16075960300 10 19 15.343055823836199 291.51806065288775 0.5909090909090909 172.26067220397914 16075960100 10 12 15.343055823836199 184.1166698860344 0.5909090909090909 108.79621402356578 16075960200 10 11 15.343055823836199 168.7736140621982 0.5909090909090909 99.7298628549353 49049001105 10 5 15.343055823836199 76.71527911918099 0.5909090909090909 45.33175584315241 16087970200 10 4 15.343055823836199 61.372223295344796 0.5909090909090909 36.265404674521925 16043970300 2 21 15.979296772500655 335.56523222251377 0.13861386138613863 46.51399258529894 16043970100 2 

In [0]:
# This shows that the tract sum vs the visitor total is pretty close. 
home_agg.filter(
    'placekey=="222-222@5w9-pn2-kxq" AND date_range_start=="2019-11-01T00:00:00-06:00"'
    ).groupBy(
        'placekey'
        ).agg(
            (F.sum('tract_visitors_scaled')).alias('Tract Sum'), 
            (F.median('raw_visitor_counts')*F.median('state_scaling')).alias('Visitor Total')
            ).display()

placekey Tract Sum Visitor Total

In [0]:
# Calculates the Sunday visits by tract
final_df = home_agg.filter(
    F.col('tract').startswith('16') # 16 is Idaho's tract number
    
).select(
    "*",
    F.month(home_agg['date_range_start']).alias('month')

).groupBy(
    'tract', 
    'month',

).agg(
    F.sum('sunday_visitors').alias('sum_sunday_visitors'),
    F.median('distance_from_home').alias('median_distance_from_home')
)

final_df.display()

tract month sum_sunday_visitors median_distance_from_home 16001000100 2 58.98440599060254 2549.0 16001000100 3 45.22172105879126 4738.0 16001000100 4 30.924086125798947 4376.0 16001000100 5 61.512978311543336 5619.0 16001000100 6 13.910846523960103 10558.5 16001000100 7 22.579367132351603 8817.0 16001000100 8 19.09624759908985 6948.0 16001000100 9 17.658216653130143 3526.0 16001000100 10 31.18245652723247 6440.0 16001000100 11 25.917201911732153 6291.0 16001000100 12 93.37219065278028 6867.0 16001000201 2 1.5791305045765354 4978.0 16001000201 3 8.201126335897309 4381.0 16001000201 4 23.565325338126666 5139.0 16001000201 5 9.40615693086377 6078.0 16001000201 6 6.365984620672865 8816.0 16001000201 7 57.627623868514306 8669.0 16001000201 8 18.759881280813257 4725.5 16001000201 9 58.21844415266792 6172.0 16001000201 10 19.210172233311624 7085.0 16001000201 11 5.443531571898032 7095.0 16001000201 12 33.05016308378258 8325.0 16001000202 2 102.89048832063199 8454.0 16001000202 3 57.69502431223958 5542.0 16001000202 4 48.12144572356002 5139.0 16001000202 5 13.542729975116167 6078.0 16001000202 6 12.738895163302274 8114.0 16001000202 7 0.0 9008.0 16001000202 8 59.50535628828973 4670.0 16001000202 9 35.97622554737871 7074.0 16001000202 10 119.52959471932067 7085.0 16001000202 11 82.12300722117837 7095.0 16001000202 12 87.92758189149512 6359.0 16001000302 2 0.9023602883294488 4978.0 16001000302 3 39.070868533802496 5251.5 16001000302 4 36.69517248249861 5139.0 16001000302 5 64.7051681611322 4741.0 16001000302 6 81.07298546318785 7218.0 16001000302 7 197.96717200284178 2421.0 16001000302 8 20.0292506199386 4524.0 16001000302 9 33.34116709028332 6172.0 16001000302 10 28.73529965836666 4481.5 16001000302 11 1.8145105239660106 6056.0 16001000302 12 61.76438751340069 6169.0 16001000303 2 8.138268260782574 7399.0 16001000303 6 83.42978828066953 3933.0 16001000303 8 29.51421430153983 20366.0 16001000303 10 32.771456290132114 9583.0 16001000303 12 35.65690948429761 6169.0 16001000304 2 22.760767026786187 4978.0 16001000304 3 76.15700399489828 6453.0 16001000304 4 73.72725710305195 5139.0 16001000304 5 82.02087995222497 5701.0 16001000304 6 70.95390933637476 4875.0 16001000304 7 57.27498394911688 102177.0 16001000304 8 7.572633560690759 4670.0 16001000304 9 84.95498313272245 6623.0 16001000304 10 100.54786015961287 6304.5 16001000304 11 61.80042291972353 7095.0 16001000304 12 163.52777103948202 6359.0 16001000400 2 59.19088222316351 6556.0 16001000400 3 89.42226965965048 9179.0 16001000400 4 55.62791231865142 5763.5 16001000400 5 43.84266525857758 5124.0 16001000400 6 72.97694192715515 8114.0 16001000400 7 36.07670093784744 9463.0 16001000400 8 27.905885519878584 4781.0 16001000400 9 179.92124310846862 2811.5 16001000400 10 56.97078433417633 2794.0 16001000400 11 66.79760031098587 7095.0 16001000400 12 40.335902455668766 4354.5 16001000500 2 105.62909871558662 4978.0 16001000500 3 32.89631199777322 5542.0 16001000500 4 78.38949717587286 4818.5 16001000500 5 48.3947825203107 5619.0 16001000500 6 104.26480188677792 7412.0 16001000500 7 61.96515866576439 2725.0 16001000500 8 57.52969018569174 4670.0 16001000500 9 45.196330785265225 6623.0 16001000500 10 11.898716483276607 6762.5 16001000500 11 132.346022674835 6056.0 16001000500 12 59.100381036702196 6731.5 16001000600 2 23.93460992311425 8748.0 16001000600 3 26.131389060039684 10500.5 16001000600 4 2.744724806450168 5139.0 16001000600 5 73.17114497042945 8475.5 16001000600 6 20.70861393595467 8816.0 16001000600 7 10.936880954732807 4806.0 16001000600 8 17.252254502392102 5864.5 16001000600 9 5.357601432661373 6172.0 16001000600 10 8.315856802349003 7085.0 16001000600 11 56.22211165579823 5888.5 16001000600 12 48.32217261750152 8325.0 16001000701 2 84.17311634613715 5622.5 16001000701 3 39.05803624783497 5839.0 16001000701 4 29.50070884562366 5775.5 16001000701 5 49.774525055439376 6151.0 16001000701 6 117.64140350569565 7878.0 16001000701 7 105.56325978934387 1804.0 16001000701 8 59.75062146892655 

In [0]:
# Calculates the Sunday visits by place (for verification purposes)
home_agg_churches = home_agg.filter(
    F.col('tract').startswith('16') # 16 is Idaho's tract number
    
    ).join(churches, ['placekey'], how='inner') # Join with churches

    
by_place = home_agg_churches.select(
    "*",
    F.month(home_agg_churches['date_range_start']).alias('month')
).groupBy(
    'placekey',
    'month'

).agg(
    F.sum('sunday_visitors').alias('sum_sunday_visitors'),
)

graph_df = home_agg_churches.select(
    "*",
).groupBy(
    'tract', 
).agg(
    (F.sum('sunday_visitors')/11).alias('sum_sunday_visitors'), # 11 months in the safegraph data
)



In [0]:
# Validate number of census tracts in Idaho, should be 298
# visits_by_tract.filter(F.col('tract').startswith('16')).count()
home_agg_churches.select(F.col('tract')).filter(F.col('tract').startswith('16')).distinct().count()

Out[46]: 289

In [0]:
# Megan's church
by_place.filter('placekey=="zzw-222@5w9-hmg-pgk"').display()
# 500-1000 Sunday visitors each month -- seems reasonable. 

placekey month sum_sunday_visitors zzw-222@5w9-hmg-pgk 10 535.0213819041235 zzw-222@5w9-hmg-pgk 8 655.7375776110822 zzw-222@5w9-hmg-pgk 3 801.2358515964291 zzw-222@5w9-hmg-pgk 11 900.904475149124 zzw-222@5w9-hmg-pgk 9 835.5301956222046 zzw-222@5w9-hmg-pgk 12 1009.604424817226 zzw-222@5w9-hmg-pgk 4 550.5460507604629 zzw-222@5w9-hmg-pgk 2 554.6678597472927 zzw-222@5w9-hmg-pgk 5 557.769903708474 zzw-222@5w9-hmg-pgk 6 973.6112893368391 zzw-222@5w9-hmg-pgk 7 829.029162556268

### 5. Visualizations

In [0]:
!pip install geopandas
!pip install folium

You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-5b8559c0-2922-4b62-8f32-7a66810be151/bin/python -m pip install --upgrade pip' command.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-5b8559c0-2922-4b62-8f32-7a66810be151/bin/python -m pip install --upgrade pip' command.


In [0]:
import geopandas as gpd
import folium

dbutils.fs.cp("dbfs:/FileStore/tl_2019_16_tract", "file:/tmp/tl_2019_16_tract", recurse = True)
gdf = gpd.read_file("/tmp/tl_2019_16_tract")
# Join graph_df and gdf
gdf = gdf.merge(graph_df.toPandas(), left_on='GEOID', right_on='tract')

In [0]:
# gdf
# Assuming gdf is your GeoPandas DataFrame containing census tracts
m = folium.Map(location=[45.697873, -114.346173], zoom_start=6)
# Convert the GeoDataFrame to a GeoJSON and add it to the folium map
gdf_json = gdf.to_json()
choropleth = folium.Choropleth(
    geo_data=gdf_json,
    data=gdf,
    columns=['tract', 'sum_sunday_visitors'],  
    key_on='feature.properties.tract', 
    fill_color='YlGn', 
    fill_opacity=0.8,
    line_opacity=0.5,
    legend_name='Sunday Visits'
)

# tooltip = folium.GeoJsonTooltip(fields=['tract', 'sum_sunday_visitors'], aliases=['Tract', 'Visitors'], localize=True)

# choropleth.add_child(tooltip)
choropleth.add_to(m)

# m


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-560169232424006>:3
      1 # gdf
      2 # Assuming gdf is your GeoPandas DataFrame containing census tracts
----> 3 m = folium.Map(location=[45.697873, -114.346173], zoom_start=6)
      4 # Convert the GeoDataFrame to a GeoJSON and add it to the folium map
      5 gdf_json = gdf.to_json()

NameError: name 'folium' is not defined

<img src = '/files/Screenshot_2023_10_31_at_8_33_14_PM.png'>
<img src ='/files/newplot__1_.png'>


### 6. Display of the first five rows of your feature table used in the visualizations

In [0]:
display(graph_df.orderBy('tract').head(5))

tract sum_sunday_visitors 16001000100 38.46542862168799 16001000201 22.925532081082704 16001000202 66.53805417020122 16001000302 51.699551779091514 16001000303 17.566378663817087